In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

from tensorflow.keras.preprocessing import image
from tensorflow.keras.utils import load_img,img_to_array
from tensorflow.keras.applications import ResNet50
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras import layers
import tensorflow as tf
from sklearn.cluster import KMeans
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from tqdm import tqdm
import os
import shutil
%matplotlib inline
# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

D0729 09:18:19.976999287      15 config.cc:119]                        gRPC EXPERIMENT tcp_frame_size_tuning               OFF (default:OFF)
D0729 09:18:19.977021972      15 config.cc:119]                        gRPC EXPERIMENT tcp_rcv_lowat                       OFF (default:OFF)
D0729 09:18:19.977025222      15 config.cc:119]                        gRPC EXPERIMENT peer_state_based_framing            OFF (default:OFF)
D0729 09:18:19.977027827      15 config.cc:119]                        gRPC EXPERIMENT flow_control_fixes                  ON  (default:ON)
D0729 09:18:19.977030395      15 config.cc:119]                        gRPC EXPERIMENT memory_pressure_controller          OFF (default:OFF)
D0729 09:18:19.977033022      15 config.cc:119]                        gRPC EXPERIMENT unconstrained_max_quota_buffer_size OFF (default:OFF)
D0729 09:18:19.977035921      15 config.cc:119]                        gRPC EXPERIMENT new_hpack_huffman_decoder           ON  (default:ON)
D0729 09:18:19.

/kaggle/input/footwearr/dataset/training/shoe boot sandal/1bdaa3e62533db7af531d2b4df4594fb.jpg
/kaggle/input/footwearr/dataset/training/shoe boot sandal/f5c3900f7823485ebe219edf3c5b4621.jpg
/kaggle/input/footwearr/dataset/training/shoe boot sandal/d985c0dd7d095da6be3dd70e02d19342.jpg
/kaggle/input/footwearr/dataset/training/shoe boot sandal/8f1db835a95da66bac80d665d6d1f935.jpg
/kaggle/input/footwearr/dataset/training/shoe boot sandal/9a0c89b4831132bf1e768f8ba2d04de5.jpg
/kaggle/input/footwearr/dataset/training/shoe boot sandal/8486b4342ea5e128e0271bd385bcc487.jpg
/kaggle/input/footwearr/dataset/training/shoe boot sandal/3b42bc2d683a30165669044f43ee81d4.jpg
/kaggle/input/footwearr/dataset/training/shoe boot sandal/408f09f88fbf8869d2c67a5253d77689.jpg
/kaggle/input/footwearr/dataset/training/shoe boot sandal/6b650513dc8b10349dfba47191c602f0.jpg
/kaggle/input/footwearr/dataset/training/shoe boot sandal/eacbf6efefc12d7b8080a9aa6bdb3a2b.jpg
/kaggle/input/footwearr/dataset/training/shoe boot

In [2]:
from tensorflow.keras.applications.vgg16 import VGG16,preprocess_input
image_path='/kaggle/input/footwearr/dataset/training'
#Define the vgg feature extractor.
vgg_model=VGG16(weights='imagenet',include_top=False)

def extract_features(image_path):
    img=image.load_img(image_path,target_size=(224,224))
    x = image.img_to_array(img)
    x = np.expand_dims(x, axis=0)
    x = preprocess_input(x)
    predictions = vgg_model.predict(x)
    predictions=predictions.flatten()
    
    return predictions


58889256/58889256 [==============================] - 0s 0us/step


In [3]:
#Create lists of features and paths.
features=[]
images_list=os.listdir('/kaggle/input/footwearr/dataset/training/shoe boot sandal')
images_list=list(map(lambda x:'/kaggle/input/footwearr/dataset/training/shoe boot sandal/'+x,images_list))

for i in tqdm(range(len(images_list))):
    filepath=images_list[i]
    img_features=extract_features(filepath)
    features.append(img_features)

  0%|          | 0/14939 [00:00<?, ?it/s]

1/1 [==============================] - 0s 313ms/step


  0%|          | 1/14939 [00:00<1:38:35,  2.53it/s]

1/1 [==============================] - 0s 83ms/step


  0%|          | 2/14939 [00:00<1:00:07,  4.14it/s]

...

100%|█████████▉| 14937/14939 [31:21<00:00,  8.36it/s]

1/1 [==============================] - 0s 70ms/step


100%|█████████▉| 14938/14939 [31:21<00:00,  8.35it/s]

1/1 [==============================] - 0s 70ms/step


100%|██████████| 14939/14939 [31:21<00:00,  7.94it/s]


In [4]:
from sklearn import manifold, decomposition
features_array = np.array(features)
print("Shape of the features before the application of the PCA transformation {}".format(features_array.shape))
pca = decomposition.PCA(n_components=0.9)
reduc_features = pca.fit_transform(features_array)
print("Shape of the features after PCA transformation {}".format(reduc_features.shape))

Shape of the features before the application of the PCA transformation (14939, 25088)
Shape of the features after PCA transformation (14939, 2537)


In [5]:
k = 3
clusters = KMeans(k)
clusters.fit(reduc_features)

/usr/local/lib/python3.8/site-packages/sklearn/cluster/_kmeans.py:1412: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)


KMeans(n_clusters=3)

In [6]:
df_results = pd.DataFrame(images_list,columns=['image_file'])
df_results["Cluster_label"] = clusters.labels_
df_results.sample(10)

image_file  Cluster_label
3306   /kaggle/input/footwearr/dataset/training/shoe ...              1
7656   /kaggle/input/footwearr/dataset/training/shoe ...              1
5791   /kaggle/input/footwearr/dataset/training/shoe ...              1
6502   /kaggle/input/footwearr/dataset/training/shoe ...              1
8372   /kaggle/input/footwearr/dataset/training/shoe ...              2
7328   /kaggle/input/footwearr/dataset/training/shoe ...              2
11541  /kaggle/input/footwearr/dataset/training/shoe ...              0
8387   /kaggle/input/footwearr/dataset/training/shoe ...              1
9730   /kaggle/input/footwearr/dataset/training/shoe ...              1
14589  /kaggle/input/footwearr/dataset/training/shoe ...              0

In [9]:
df_results.head()
os.makedirs('/kaggle/working/image1')
os.makedirs('/kaggle/working/image2')
os.makedirs('/kaggle/working/image3')
path1='/kaggle/working/image1'
path2='/kaggle/working/image2'
path3='/kaggle/working/image3'


FileExistsError: [Errno 17] File exists: '/kaggle/working/image1'

In [20]:
for index,row in df_results.iterrows():
    if row['Cluster_label']==0:
        shutil.copy(row['image_file'], '/kaggle/working/image1')
    elif row["Cluster_label"]==1:
        shutil.copy(row['image_file'], '/kaggle/working/image2')
    else:
        shutil.copy(row['image_file'], '/kaggle/working/image3')

In [25]:
import zipfile
import os
from IPython.display import FileLink

def zip_dir(directory = '/kaggle/working/', file_name = 'directory.zip'):
     os.chdir(directory)
     zip_ref = zipfile.ZipFile(file_name, mode='w')
     for folder, _, files in os.walk(directory):
         for file in files:
             if file_name in file:
                 pass
             else:
                 zip_ref.write(os.path.join(folder, file))

     return FileLink(file_name)

In [26]:
zip_dir()

/kaggle/working/directory.zip